In [1]:
import kaleido
import numpy as np
import pandas as pd

In [1]:
# Solicitud de datos a la API REST
from api_somo import APIClient, fetch_qf 
import logging

# Setting up logging for the main script
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

api_url = "http://127.0.0.1:8000/database/functions/time-series/filter_date_serie/"
params = {
    "station_name": "tumaco",
    "variable_name": "nivel del mar",
    "processing_level_name": "Control de calidad",
    "start_date":"2009-01-01",
    "end_date":"2012-12-31"
    }

try:
    # 1. Fetch and process the data
    historical_series = APIClient.fetch_and_process_data(api_url, params)

    if historical_series.empty:
        raise ValueError("The historical series is empty.")

    # Additional processing with the historical series
    logger.info(f"Fetched historical series: {historical_series.head(0)}")

    if historical_series.empty:
        raise ValueError("The historical series is empty.")

    # Additional processing with the historical series
    logger.info(f"Fetched historical series: {historical_series.head(0)}")

except Exception as e:
    logger.error(f"Error fetching historical series: {e}")
historical_series

display(historical_series.columns)
display(round(historical_series.describe(),3))

INFO:api_somo:Sending request to http://127.0.0.1:8000/database/functions/time-series/filter_date_serie/ with parameters: {'station_name': 'tumaco', 'variable_name': 'nivel del mar', 'processing_level_name': 'Control de calidad', 'start_date': '2009-01-01', 'end_date': '2012-12-31'}
INFO:api_somo:Original columns: ['date_time', 'sensor_data', 'quality_flag']
INFO:api_somo:Columns after renaming: ['timestamp', 'value', 'qf']
INFO:api_somo:Timestamp conversion and indexing complete.
INFO:__main__:Fetched historical series: Empty DataFrame
Columns: [value, qf]
Index: []
INFO:__main__:Fetched historical series: Empty DataFrame
Columns: [value, qf]
Index: []


Index(['value', 'qf'], dtype='object')

value           qf
count  2057377.000  2057377.000
mean    -54773.723        5.406
std      49773.242        3.964
min     -99999.000        1.000
25%     -99999.000        1.000
50%     -99999.000        9.000
75%          4.070        9.000
max        634.880        9.000

In [3]:
historical_series.index.dtype

datetime64[ns, UTC]

# Análisis exploratorio

In [4]:

#serie_historica = reshample_time_serie(serie_historica, 'D', 'sum')
historical_series = categorize_precipitation(historical_series, params)
print(round(historical_series.describe(),2))


          value        qf
count  21601.00  21601.00
mean   -2647.92      1.21
std    16056.08      1.28
min   -99999.00      1.00
25%        0.00      1.00
50%        0.00      1.00
75%        0.00      1.00
max       16.70      9.00


## Preprocesamiento
convertir en nan los valores que tengan bandera de calidad distina a 1

In [5]:
# PRE-PROCESAMIENTO DE LAS SERIES
#convertir en NaN los registros con qf distinto de 1
from utils.utils import reshample_time_serie

historical_series.loc[historical_series['qf'] != 1, 'value'] = np.nan
resample_serie = reshample_time_serie(historical_series,nueva_frecuencia='ME', metodo='sum')

## Paso 2: visualizar el set de datos
Para entender cómo estan distribuidas las variables de nuestro dataset podemos realizar una gráfica de cada una de estas series de tiempo.

En este caso podemos usar el método plot incluído en el DataFrame de Pandas (df)

In [6]:
"""from tkinter.messagebox import NO
from graphics_utils.express import fig_lineplot

fig_historical=fig_lineplot(historical_series,params=params,color=None)
fig_resample= fig_lineplot(resample_serie, params=params, color=None)

fig_historical.show()
fig_resample.show()"""

'from tkinter.messagebox import NO\nfrom graphics_utils.express import fig_lineplot\n\nfig_historical=fig_lineplot(historical_series,params=params,color=None)\nfig_resample= fig_lineplot(resample_serie, params=params, color=None)\n\nfig_historical.show()\nfig_resample.show()'

## Paso 3: análisis de datos faltantes
Los datos faltantes serán simplemente aquellas celdas dentro del set de datos que no contienen cantidades numéricas.

Usualmente estas celdas contendrán valores tipo NaN (o Not A Number) y las podemos encontrar fácilmente usando la función isna() de Pandas:

In [7]:
print('Cantidad de NaNs:')
for column in historical_series:
    nans = historical_series[column].isna().sum()
    print(f'\tColumna {column}: {nans}')

Cantidad de NaNs:
	Columna value: 572
	Columna qf: 0
	Columna category: 0


Con las anteriores líneas de código podemos analizar cada columna del dataset y calcular e imprimir en pantalla la cantidad total de datos faltantes, obteniendo este resultado:

## Paso 4: Análisis de la periodicidad del dataset
En este paso debemos verificar si entre muestras consecutivas del set de datos existe una diferencia temporal de exactamente 1 hora.

Esta verificación es clave para garantizar que los modelos LSTM que implementaremos más adelante aprenderán a detectar adecuadamente los patrones en la serie de tiempo.

Para verificar esta periodicidad podemos simplemente tomar el índice del dataset, que se encuentra en formato datetime y usar la función diff para calcular las diferencias entre instantes de tiempo consecutivos.

Idealmente estas diferencias deberían ser de exactamente 3.600 segundos (o 1 hora) en todos los casos:

In [8]:
df_time_diffs = historical_series.index.to_series().diff().dt.total_seconds()
print('tiempo en minutos', df_time_diffs.value_counts()/60)


tiempo en minutos timestamp
600.0    360.0
Name: count, dtype: float64


# Pre-procesamiento
En esta fase nos enfocaremos en dos tareas:

El manejo de datos faltantes y
El ajuste de la periodicidad del dataset
Veamos en primer lugar cómo realizar el manejo de datos faltantes en este caso particular.

## Paso 1: manejo de datos faltantes
Como lo vimos hace un momento durante el análisis exploratorio, algunas columnas de nuestro dataset contienen datos faltantes. En particular:

Dado el reducido número de datos faltantes, podemos usar una simple interpolación para completarlos.

Para esto podemos simplemente usar el método interpolate(method='linear') de la librería Pandas:

In [9]:
print('Cantidad de NaNs:')
for column in historical_series:
    nans = historical_series[column].isna().sum()
    print(f'\tColumna {column}: {nans}')


Cantidad de NaNs:
	Columna value: 572
	Columna qf: 0
	Columna category: 0


## Paso 2: ajuste de periodicidad
Durante el análisis exploratorio vimos que la mayoría de los registros (50.189) tienen una periodicidad de exactamente 1 hora. Sin embargo, unos pocos registros tienen periodicidades ligeramente por encima o por debajo de este valor.

En este segundo paso del pre-procesamiento corregiremos este comportamiento.

Comenzaremos corrigiendo aquellos registros cuyas diferencias temporales (entre pares consecutivos de registros) son exactamente iguales a 0.0 segundos. Estas diferencias de 0 s indican que la marca temporal (fecha y hora de cada registro) es exactamente la misma, lo cual nos indica que simplemente se trata de registros repetidos.

Para eliminar estos registros repetidos podemos usar el método drop_duplicates de Pandas:

In [10]:
#historical_series.drop_duplicates(keep='first', inplace=True, ignore_index=False)

Y tras ejecutar esta línea de código podemos recalcular las diferencias temporales consecutivas:

In [11]:
#df_time_diffs = historical_series.index.to_series().diff().dt.total_seconds()
#print(df_time_diffs.value_counts())

In [15]:
from sklearn.impute import KNNImputer

# Crear el imputador KNN con pesos basados en la distancia
imputer = KNNImputer(n_neighbors=5, weights="distance")

# Imputar solo la columna 'value'
interpolated_data = imputer.fit_transform(historical_series[['value']])

# Crear la columna 'valueImp' con los valores imputados por KNN
historical_series['valueImp'] = interpolated_data[:, 0]

# Opción 4: Interpolación lineal para la columna 'value'
historical_series_resampled_interpolate = historical_series[['value']].asfreq('T').interpolate(method='spline', order=3)

# Asegúrate de reemplazar 'valueImp' con la interpolación, si deseas usarla.
historical_series['valueImp'] = historical_series_resampled_interpolate['value']

# Verificar la cantidad de NaNs en cada columna después de la imputación
dataset = historical_series[['value', 'valueImp']]

print('Cantidad de NaNs:')
for column in dataset:
    nans = dataset[column].isna().sum()
    print(f'\tColumna {column}: {nans}')
    
# Mostrar resultados
print(dataset)


Cantidad de NaNs:
	Columna value: 572
	Columna valueImp: 0
                           value  valueImp
timestamp                                 
2010-01-01 05:00:00+00:00    0.0       0.0
2010-01-01 05:10:00+00:00    0.0       0.0
2010-01-01 05:20:00+00:00    0.0       0.0
2010-01-01 05:30:00+00:00    0.0       0.0
2010-01-01 05:40:00+00:00    0.0       0.0
...                          ...       ...
2010-05-31 04:20:00+00:00    0.0       0.0
2010-05-31 04:30:00+00:00    0.0       0.0
2010-05-31 04:40:00+00:00    0.0       0.0
2010-05-31 04:50:00+00:00    0.0       0.0
2010-05-31 05:00:00+00:00    0.0       0.0

[21601 rows x 2 columns]


C:\Users\dreng\AppData\Local\Temp\ipykernel_12016\715507120.py:13: FutureWarning:

'T' is deprecated and will be removed in a future version, please use 'min' instead.



In [16]:
import matplotlib.pyplot as plt

# Resampleo de datos para mensual
#dataset = dataset.resample('D').sum()

# Crear la columna 'dif' en el DataFrame
dataset['dif'] = dataset['valueImp'] - dataset['value']
dataset['valueImp-dif']=dataset['valueImp']-dataset['dif']

print('Cantidad de NaNs:')
for column in dataset:
    nans = dataset[column].isna().sum()
    print(f'\tColumna {column}: {nans}')

import plotly.graph_objects as go

# Crear una figura
fig = go.Figure()

# Iterar sobre todas las columnas del dataset y agregar la serie de tiempo a la figura
for column in dataset.columns:
    fig.add_trace(go.Scatter(x=dataset.index, y=dataset[column], mode='lines+markers', name=column))

# Etiquetas y título
fig.update_layout(
    title="Series de Tiempo para todas las columnas",
    xaxis_title="Fecha",
    yaxis_title="Valor",
    template="plotly_dark",
)

# Mostrar el gráfico
fig.show()


C:\Users\dreng\AppData\Local\Temp\ipykernel_12016\4055242433.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



Cantidad de NaNs:
	Columna value: 572
	Columna valueImp: 0
	Columna dif: 572
	Columna valueImp-dif: 572


In [ ]:
from tkinter.messagebox import NO
from graphics_utils.express import fig_lineplot

fig_historical=fig_lineplot(historical_series,params=params,color=None)
fig_resample= fig_lineplot(resample_serie, params=params, color=None)

fig_historical.show()
fig_resample.show()

In [15]:
#historical_series.to_csv('tum_prec_cc_2009.csv')